In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import entry_to_dict #read_publications, read_addresses, read_seminars

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
#from research.models import Publication


#from home.models import Room, Country, Title_full, Gender, Status
#from internal.models import Member
from external.models import News
#from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

#import gender_guesser.detector as gender
import re


## Write old papers database

In [2]:
def read_addresses(file_name):
    
    with open(file_name, 'r') as file:
            content = file.read() 
    all_entries = content.split('enditem')
    
    for entry in all_entries:
        dictio = entry_to_dict(entry)
        if dictio != {}:
            try:
                df = df.append(dictio, ignore_index=True)     # append new entry to DF
            except:
                df = pd.DataFrame(dictio, index=[0])          # first time create the DF
    df = df.fillna(np.NaN)
    #ind = df[df['vorname'].isna() & df['nachname'].isna()].index.values
    #df.drop(ind,inplace=True)
    return df

In [3]:
path_news = 'old_database/database.news'
df_news = read_addresses(path_news)

# take only publications with DOI
#df_papers = df_papers[~df_papers['DOI'].isnull()]

# only publications with reference
#df_papers = df_papers[~df_papers['reference'].isnull()]
# df_papers = df_papers[~(df_papers['type']=='inbook')]

In [4]:
df_news

﻿image  year month  monthname day    dayname  \
0    2019_10_22_G_Cuniberti_EurASc  2019    10    October  22    Tuesday   
1                              NaN  2019    09  September  27     Friday   
2                              NaN  2019    09  September  27     Friday   
3                              NaN  2019    06       June  14     Friday   
4                              NaN  2019    02   February  27  Wednesday   
..                             ...   ...   ...        ...  ..        ...   
220                            NaN  2003    05        May  20    Tuesday   
221                            NaN  2003    05        May  02     Friday   
222                            NaN  2003    03      March  13   Thursday   
223                            NaN  2003    02   February  02     Sunday   
224                            NaN  2003    01    January  01  Wednesday   

      hour                                              title  \
0    10:00  Prof. Cuniberti appointed as Fellow of the Eur...   
1    13:00  Prof. Cuniberti appointed as Guest Professor a...   
2    12:00  Science without borders: Materials researchers...   
3    18:00  Over 130 kids and families at our chair during...   
4    14:00  TU Dresden is at the forefront in materials sc...   
..     ...                                                ...   
220               Small is great! (feature article in U-Mail)   
221  08:30                        Gr&uuml;&szlig; Gott Rafael   
222  08:30      1st EU-net theory group meeting at Regensburg   
223  08:30    New EU project: "DNA-based molecular nanowires"   
224  14:00                                           arrived!   

                                           preabstract  \
0    During its 2019 Ceremony of Awards, held on Oc...   
1    On September 27th, 2019, Prof. Gianaurelio Cun...   
2    On September 27th, 2019, materials scientists ...   
3    At this special day of the year, people of all...   
4    In the current QS University Ranking, TU Dresd...   
..                                                 ...   
220  The May issue of the University Journal (Pages...   
221  Welcome to Rafael Guti&eacute;rrez who has sta...   
222  kick-off meeting of the theory group of the <a...   
223  Kick-off meeting of the EU project IST-2001-38...   
224  Juyeon Yi and Giovanni Cuniberti start on 01.0...   

                                              abstract  \
0    He has been elected as Fellow of the Materials...   
1    Prof. Zhongqin Lin, President of SJTU, handed ...   
2    The agreement is being signed during a delegat...   
3    We offered interactive presentations and exper...   
4    In the "QS World University Ranking by Subject...   
..                                                 ...   
220                                                NaN   
221                                                NaN   
222  <h4>scope</h4>\t<ul>\t<li>collecting a list of...   
223  An international consortium of 7 universities ...   
224                                                NaN   

                                        image imagelink Institut  \
0                                         NaN       NaN      NaN   
1    2019_09_27_Guest_Professorship_Cuniberti       NaN      NaN   
2                     2019_09_27_MOU_Shanghai       NaN      NaN   
3                                   2019_LNDW       NaN      NaN   
4                             2019_QS-Ranking       NaN      NaN   
..                                        ...       ...      ...   
220                       2003_05_umail_small       NaN      NaN   
221  2004_03_25_28_sankt_englmar_1044_cropped       NaN      NaN   
222          1493_stadtansicht_von_regensburg       NaN      NaN   
223                           2003_03_nanodna       NaN      NaN   
224                                2003_01_jy       NaN      NaN   

                                                     title_here  
0                          NaN                           

In [5]:
df_news.columns

Index(['﻿image', 'year', 'month', 'monthname', 'day', 'dayname', 'hour',
       'title', 'preabstract', 'abstract', 'image', 'imagelink', 'Institut',
       '', 'title_here'],
      dtype='object')

**Write to Django Database**

In [6]:
for index, row in df_news.iterrows():
    ref=row['year']
    try:
        year = ref.split(' ')[1]
    except:
        print (ref)
        
    month=row['month']
    try:
        month = ref.split(' ')[1]
    except:
        print (ref)
    day=row['day']
    try:
        day = ref.split(' ')[1]
    except:
        print (ref)
    for c in day:
        if c=='-':
            day=day.split('-')[0]
            print(day, 'DAAAAAAAAAAAAAAAAAAAY')
            break
        if c=='+':
            day=day.split('+')[0]
            print(day, 'DAAAAAAAAAAAAAAAAAAAY')
            break
        if c==',':
            day=day.split(',')[0]
            print(day, 'DAAAAAAAAAAAAAAAAAAAY')
            break
    hour=row['hour']
    try:
        hour = ref.split(' ')[1]
    except:
        print (ref)
    
    try:    
        title_raw = html.unescape(row['title'])
    except:
        title_raw= html.unescape(row['title_here'])
    preabstract_raw = html.unescape(row['preabstract'])
    try:
        abstract_raw= row['abstract']
    except:
        abstract_raw = None
    if type(row['image']) == float:
        image_raw = None
    else:
        if row['image'].split('/')[-1].split('.')[-1]=='jpg':
            image_raw = 'uploads/news/img/' + row['image'].split('/')[-1]
        else:
            image_raw = 'uploads/news/img/' + row['image'].split('/')[-1]+'.jpg'
    if type(row['imagelink']) == float:
        image_url_raw = None
    else:
        image_url_raw = row['imagelink'].split(' ')[-1]
    pubdate = f"{row['year']}-{month}-{day}"
    if type(row['abstract'])==float: abstract_raw=''
    if type(row['preabstract'])==float: preabstract_raw=''
    new_news = News(      title=title_raw,
                          abstract=preabstract_raw+abstract_raw,
                          pub_date=pubdate,
                          image=image_raw,
                          image_url=image_url_raw
                        )
    new_news.save()

2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2019
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2018
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2017
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2016
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015
2015


Old stuff:

In [ ]:
len(df_papers['DOI'].unique())

In [ ]:
df_papers[df_papers.duplicated(subset='DOI', keep=False)][['title','DOI','year','cvselected','type']]

In [ ]:
df_papers['type'].unique()

In [ ]:
for col in df_papers.isna().sum().sort_values().index.values:
    try:
        print (col,'\t\tNaN_count:',df_papers[col].isnull().value_counts()[1])
    except:
        print (col,'ALL')

In [ ]:
df_papers[df_papers['reference'].isnull()][['title','DOI','year']]

## Patents and Thesis

## Nanoseminars

In [ ]:
path_seminars = 'old_database/database.seminars_22_07_2021'
df_seminars = read_seminars(path_seminars) 

In [ ]:
df_seminars.columns

In [ ]:
df_seminars[df_seminars['room'].isna()]

In [ ]:
url=None
for index, row in df_seminars.iterrows():
    date = f"{row['year']}-{row['month']}-{row['day']}"
    title =  html.unescape(row['title'])
    if type(row['affiliation']) != float:
        affil =  html.unescape(row['affiliation'])
    else:
        affil = None
    if type(row['room']) != float:
        room = html.unescape(row['room'])
    else:
        room = None
        if room == 'Zoom meeting':
            url = 'https://tinyurl.com/nanoSeminar-GA'
        else:
            url = None
    if type(row['hour']) != float:
        hour = row['hour'].strip().split(' ')[0].replace('<b>','').replace('</b>','')
    else:
        hour = '10:00'
    date = date + f' {hour}:00'
#     print (html.unescape(row['speaker']))
    room = None
    
    if type(row['talkabstract']) != float:
        abstract = html.unescape(row['talkabstract']).rsplit('<br>  <br> <h3>')[0].rsplit('<br><br> <h3>')[0].rsplit('<br> <h3><a')[0].rsplit('<br>20<a')[0].rsplit('<br><br>  <h3><a')[0]
    else:
        abstract = None
        
    if type(row['announcementpdf']) != float:
        announcement = row['announcementpdf']
#         print (announcement)
    else:
        announcement = None
        
    if type(row['semimage']) != float:
        if row['semimage'].strip() =='':
            image= None
        else:
            image = 'uploads/members/img/' + row['semimage'].strip() + '.jpg'
    
    else:
        image = None
    if type(row['sliderefpdf']) != float:

        slides= row['sliderefpdf'].split('/')[-1]
        if slides.strip() == '':
            slides = None
        else:
            slides = 'uploads/teaching/seminar/' + slides
            print (slides)
    else:
        slides = None
    speaker = html.unescape(row['speaker'])
    new_seminar = Seminar(start_time=date, title=title, abstract=abstract,
                          speaker_name=speaker, speaker_affiliation=affil,
                          image=image, slides=slides, video_conf=url
                        )
    
    new_seminar.save()
        
    

In [ ]:
df_seminars['room'].unique()

## Create Members, Rooms, Academic Titles, Countries

In [ ]:
path_members = 'old_database/database.addresses_chair'
members = read_addresses(path_members)
members.head()

###  Countries

In [ ]:
def set_country(country_old):
    try:
        if country_old in ['Germany','German','Deutsch','Deitsch']:
            return 'German'
        elif country_old in ['Russia','Russian']:
            return'Russia'
        elif country_old in ['Italy','Italian']:
            return 'Italy'
        elif country_old in ['Spain','Spanish']:
            return 'Spain'
        elif country_old in ['Columbia','Colombia']:
            return 'Colombia'
        elif country_old in ['China','Chinese']:
            return 'China'
        elif country_old in ['Greece','Greek']:
            return 'Greece'
        elif country_old in ['India','Indian']:
            return 'India'
        elif country_old in ['Iran','Iranian']:
            return 'Iran'
        elif country_old in ['Mexico','Mexiko']:
            return 'Mexico'
        elif country_old in ['Korea', 'Korean']:
            return 'Korea'
        elif country_old in ['Poland', 'Polish']:
            return 'Poland'
        elif country_old in ['Portugal', 'Portuguese']:
            return 'Portugal'
        elif country_old in ['Turkey', 'Turkish']:
            return 'Turkey'
        
        elif country_old in ['Ukrain', 'Ukraine']:
            return 'Ukraine'
        elif country_old.strip() == '':
            return None
        elif type(country_old) == float:
            return None
        else:
            return country_old
    except:
        print('problems in country', country_old)
        return None
    

In [ ]:
# clean countries:
for index, row in members.iterrows():
    members.loc[index,'nationality'] = set_country(row['nationality'])
members.nationality.unique()

In [ ]:
# # fill country class
# for country in members.nationality.unique():
#     if country != None:
#         new_country = Country(name=country)
#         new_country.save()

### Titles

In [ ]:
def set_title(title_old):
    try:
        if 'DIPL' in title_old.upper():
            return 'Dipl.'
        elif title_old.strip() =='Ms.' or title_old.strip() =='Ms':
            return 'Ms.'
        elif title_old.strip() =='Mr.' or title_old.strip() =='Mr':
            return 'Mr.'
        elif title_old.strip() in ['M. Sc.','MSc.','M.Sc.']:
            return 'M.Sc.'
        elif title_old.strip() in ['B. Sc.','BSc.','B.Sc.']:
            return 'B.Sc.'
        elif title_old.strip()[0:2] == 'Dr' or title_old.strip() in ['PhD']:
            return 'Dr.'
        elif 'Prof' in  title_old.strip():
            return 'Prof.'
        elif 'PD Dr.' == title_old[0:6]:
            return 'PD Dr.'
        elif 'M.A.' == title_old.strip():
            return 'M.A.'
        else:
            print('problems in title', title_old)
            return None
    except:
        return None
    
    return title

def set_last_name(row):
    if type(row['nachname']) != float:
        return html.unescape(row['nachname'])
    else:
        return html.unescape(row['nachnameweb'])

def set_education(education):
    if type(row['education']) == float or row['education'].strip()=='':
        return None
    else:
        return html.unescape(row['education'])

In [ ]:
for index, row in members.iterrows():
    members.loc[index,'titlefull'] = set_title(row['titlefull'])
members.titlefull.unique()

In [ ]:
# for title in members.titlefull.unique():
#     if title != None:
#         new_title = Title_full(title_short=title, title=title)
#         new_title.save()

### Status

In [ ]:
members.status.unique()

In [ ]:
options = ['professor', 'PhD student', 'senior scientist', 'postdoc', 'research assistant', 'secretariat']
# # fill Status class
for status in options:
    new_status = Status(name=status)
    new_status.save()

### Write Members

In [ ]:
members[members['former']!='yes'][['sort_status','nachname']]

In [ ]:
for room in members[members['former'] != 'yes']['room'].unique():
    try:
        id = Room.objects.filter(name__icontains=room.split(' ')[-1])[0].id
        print(room, Room.objects.get(pk=id).name)
    except:
        print(f'room{room} not found')


In [ ]:
options = ['professor', 'PhD', 'senior scientist', 'postdoc', 'research assistant', 'secretariat']
for index, row in members.iterrows():
    
    nachname = set_last_name(row)
    print (nachname)
    vorname = html.unescape(row['vorname'])
    education = set_education(row['education'])
    picture = 'uploads/members/img/' + row['passphoto'].strip() + '.jpg'
    
    member = Member(last_name=nachname, given_name=vorname, education=education, image=picture)
    member.save()
    
    try:
        member.sort_status = row['sort_status'].strip()
    except:
        pass
    try:
        if 'visit' in row['sort_status']:
            member.visitor = True
        else:
            member.visitor = False
    except:
        pass
    
        
    if row['former'] == 'yes':
        member.active = False

        if type(row['formerstartdate']) == float:
            entry_date = f"2010-01-01"
        else:
            entry_date = f"{row['formerstartdate']}-01-01"
        
        exit_date = f"{row['formerenddate']}-12-30"
        member.entry_date = entry_date
        member.exit_date = exit_date
    else:
        member.active = True
        # find room
        try:
            idd = Room.objects.filter(name__icontains=row['room'].split(' ')[-1])[0].id
            room = Room.objects.get(pk=idd)
            member.room.add(room)
        except:
            pass
    

        if (type(row['tel'])==float) or (row['tel'].strip()) == '' or (row['tel']=='Wirtschaftskauffrau') :
            pass
        else:
            member.job_phone = row['tel']
    
    if type(row['briefbio']) == float or row['briefbio'].strip() == '':
        pass
    else:
        member.bio = html.unescape(row['briefbio'])

    
    
    # find country
    try:
        idd = Country.objects.filter(name__icontains=row['nationality'])[0].id
        country = Country.objects.get(pk=idd)
        member.country = country
    except:
        pass
    
    # find title
    try:
        idd = Title_full.objects.filter(title_short__icontains=row['titlefull'])[0].id
        title = Title_full.objects.get(pk=idd)
        member.title = title
    except:
        pass
    
    # Gender
    
    try:
        gender = define_gender(vorname)
        idd = Gender.objects.filter(name__icontains=gender)[0].id
        gender = Gender.objects.get(pk=idd)
        member.gender = gender
        
    except:
        pass
    
    # Status
    try:
        status_db = row['status'].split('(')[0].strip()
        idd = Status.objects.filter(name__icontains=status_db)[0].id
        status = Status.objects.get(pk=idd)
        member.status = status
    except:
        pass
    
    member.save()
    try:
        if type(row['birth_year']) == float or row['birth_year'].strip()=='' or '?' in row['birth_year'] or 'X' in row['birth_year'] or '-' in row['birth_year'] :
            pass
        else:
            member.birth_day = f"{row['birth_year']}-{row['birth_month']}-{row['birth_day']}"
            member.save()
    except:
        pass
    
    